# Evidencia 1. Actividad Integradora
## Parte 1. Sistemas multiagentes

Ruy Guzmán Camacho | A01639912

Adrián Becerra Meza | A01639813

Santiago González de Cosío Romero | A01640329

#### Librerías


In [5]:
#model design
import agentpy as ap

#visualizations
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import random
import time

### Definición de modelo

In [6]:
pos = [0, 1]
moves = [(0,-1), (1, 0)]


class StreetModel(ap.Model):
    def setup(self):

        # auxiliar variables for positioning cars
        self.h_count = 0
        self.v_count = 0

        # Create agents (trees)
        n_trees = int(self.p['Tree density'] * (self.p.size**2))
        trees = self.agents = ap.AgentList(self, n_trees)
        self.carros = ap.AgentList(self, self.p['trafico'])

        # Create grid (street)
        self.street = ap.Grid(self, [self.p.size]*2, track_empty=True)
        self.street.add_agents(trees, random=True, empty=True)
        self.street.add_agents(self.carros,[(2,30)]*self.p['trafico'])

        # Initiate a dynamic variable for all elements
        # Condition 0: trees, 1: car, 2: street 
        # position 0: top, 1: left
        # Draw trees
        self.agents.condition = 0
    
        # Draw Street
        street1 = self.street.agents[0:self.p.size, int(self.p.size*0.5)-5:int(self.p.size*0.5)+5]
        street2 = self.street.agents[int(self.p.size*0.5)-5:int(self.p.size*0.5)+5, 0:self.p.size]
        street1.condition = 2
        street2.condition = 2

        # draw cars
        self.carros.condition = 1

        # position cars
        for carro in self.carros:
            carro.position = random.choice(pos)
            if carro.position == 0:
                self.h_count += 1
                #horizontal
                self.street.move_to(carro, (int(self.p.size*0.5),2))
            else:
                #vertical
                self.v_count += 1
                self.street.move_to(carro, (2,int(self.p.size*0.5)))



    def step(self):

        # Select cars
        carros = self.carros

        # move cars depending on position
        for carro in carros:
            if carro.position == 1:
                self.street.move_by(carro, (random.choice(pos),0))
            else:
                self.street.move_by(carro, (0,random.choice(pos)))


        burning_trees = self.agents.select(self.agents.condition == 0)
        if len(burning_trees) == 0:
            self.stop()


    def end(self):
        
        # Document a measure at the end of the simulation
        burned_trees = len(self.agents.select(self.agents.condition == 2))
        self.report('Percentage of burned trees',
                    burned_trees / len(self.agents))
                    

### Parametros

In [7]:
# Define parameters

parameters = {
    'Tree density': 1, # Percentage of grid covered by trees
    'size': 90,
    'n': 20, # Height and length of the grid
    'steps': 200,
    'trafico': 10
}


### Renderizado

In [8]:
# Create single-run animation with custom colors

def animation_plot(model, ax):
    attr_grid = model.street.attr_grid('condition')
    color_dict = {0:'#7FC97F', 1:'#d62c2c', 2:'#808080', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a forest fire\n"
                 f"Time-step: {model.t}, Trees left: "
                 f"{len(model.agents.select(model.agents.condition == 0))}")

fig, ax = plt.subplots()
model = StreetModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=60))